In [4]:
import pandas as pd
import numpy as np
import itertools
import math
import time
import gensim
from collections import Counter
from gensim.parsing.preprocessing import remove_stopwords
from nltk.tokenize import word_tokenize
from gensim.models import Doc2Vec
import multiprocessing
from multiprocessing import Process
import pickle

In [3]:
df1=pd.read_json("jsons/dblp-ref-0.json",lines=True)
df2=pd.read_json("jsons/dblp-ref-1.json",lines=True)
df3=pd.read_json("jsons/dblp-ref-2.json",lines=True)
df4=pd.read_json("jsons/dblp-ref-3.json",lines=True)
frames=[df1,df2,df3,df4]

KeyboardInterrupt: 

In [3]:
df=pd.concat(frames)
df.head()

abstract  \
0  The purpose of this study is to develop a lear...   
1  This paper describes the design and implementa...   
2  This article applied GARCH model instead AR or...   
3                                                NaN   
4                                                NaN   

                                             authors  \
0  [Makoto Satoh, Ryo Muramatsu, Mizue Kayama, Ka...   
1                        [Gareth Beale, Graeme Earl]   
2  [Altaf Hossain, Faisal Zaman, Mohammed Nasser,...   
3  [Jea-Bum Park, Byungmok Kim, Jian Shen, Sun-Yo...   
4                [Giovanna Guerrini, Isabella Merlo]   

                                     id  \
0  00127ee2-cb05-48ce-bc49-9de556b93346   
1  001c58d3-26ad-46b3-ab3a-c1e557d16821   
2  001c8744-73c4-4b04-9364-22d31a10dbf1   
3  00338203-9eb3-40c5-9f31-cbac73a519ec   
4  0040b022-1472-4f70-a753-74832df65266   

                                          references  \
0  [51c7e02e-f5ed-431a-8cf5-f761f266d4be, 69b625b...   
1  [10482dd3-4642-4193-842f-85f3b70fcf65, 3133714...   
2  [2d84c0f2-e656-4ce7-b018-90eda1c132fe, a083a1b...   
3  [8c78e4b0-632b-4293-b491-85b1976675e6, 9cdc54f...   
4                                                NaN   

                                               title  \
0  Preliminary Design of a Network Protocol Learn...   
1  A methodology for the physically accurate visu...   
2  Comparison of GARCH, Neural Network and Suppor...   
3  Development of Remote Monitoring and Control D...   
4  Reasonig about Set-Oriented Methods in Object ...   

                                               venue  year  
0  international conference on human-computer int...  2013  
1            visual analytics science and technology  2011  
2       pattern recognition and machine intelligence  2009  
3                                                     2011  
4                                                     1998

In [4]:
df.drop(['id','references','title','venue'],axis=1,inplace=True)

In [5]:
print("With Nan: ",df.shape)
df.dropna(inplace=True)
print("Without Nan: ",df.shape)

With Nan:  (3079007, 3)
Without Nan:  (2548530, 3)


In [6]:
def handle_abstract(old_abstract):
    if 'Background#R##N#' in old_abstract:
        return(old_abstract[16:])
    return(old_abstract)

In [7]:
df['abstract'] = df['abstract'].apply(handle_abstract)
df=df.sort_values('year')
df=df.reset_index(drop=True)

In [8]:
df.shape

(2548530, 3)

In [9]:
df=df.drop(df[df.authors.map(len)<2].index)
df=df.reset_index(drop=True)

In [10]:
df.shape

(2258334, 3)

In [11]:
def extract_coauthors(df):
    coauthor_list=[]
    for i in range(df.shape[0]):
        if(i%10000==0):
            print(i//10000,end=' ')
        comb=list(itertools.combinations(df.iloc[i].authors, 2))
        coauthor_list.extend(list(map(lambda data: (data,df.iloc[i].year),comb)))

    return coauthor_list

In [12]:
coauthor_list=extract_coauthors(df)

0 1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 125 126 127 128 129 130 131 132 133 134 135 136 137 138 139 140 141 142 143 144 145 146 147 148 149 150 151 152 153 154 155 156 157 158 159 160 161 162 163 164 165 166 167 168 169 170 171 172 173 174 175 176 177 178 179 180 181 182 183 184 185 186 187 188 189 190 191 192 193 194 195 196 197 198 199 200 201 202 203 204 205 206 207 208 209 210 211 212 213 214 215 216 217 218 219 220 221 222 223 224 225 

In [13]:
pickle.dump(coauthor_list,open("coauthor_list_dl.pkl","wb"))

In [14]:
author_dict=dict()

for coauthor,score in coauthor_list:
    author_dict[coauthor[0]] = ''
    author_dict[coauthor[1]] = ''

In [ ]:
count = 0
for i in range(df.shape[0]):
    if count%100000 == 0:
        print(count//100000,end=' ')
    count+=1
    for author in df.iloc[i].authors:
        author_dict[author] += df.iloc[i].abstract

0 1 2 3 4 5 6 7 8 9 10 

In [ ]:
present_year=df['year'].max()

In [ ]:
%%time
coauthor_set = Counter()
for k,v in coauthor_list:
    coauthor_set[tuple(sorted(k))] += 1/math.log(present_year-v+2,2)

In [ ]:
coauthor_set=list(coauthor_set.items())

In [ ]:
len(coauthor_set)

In [ ]:
# main_df = {'Author1':[], 'Author2':[], 'Score':[]}
# for coauthor,score in coauthor_set:
#     main_df['Author1'].append(coauthor[0])
#     main_df['Author2'].append(coauthor[1])
#     main_df['Score'].append(score)
# main_df=pd.DataFrame(main_df)

In [ ]:
# /main_df['Score']=(main_df['Score']-main_df['Score'].min())/(main_df['Score'].max()-main_df['Score'].min())

In [ ]:
# author_dict.keys()

In [ ]:
# author_dict['Angel Gomez-Sacristan']

In [5]:
model=Doc2Vec.load('others/doc2vec_model_50')

In [ ]:
count = 0
author_vector_dict=dict()
start=time.time()
for author in author_dict:
    if count% 10000 == 0:
        print(count//10000,end=' ')
        print(time.time()-start,end=' ')
    count+=1
    preprocessed_abstract=gensim.utils.simple_preprocess(remove_stopwords(author_dict[author]))
    author_vector_dict[author]=list(model.infer_vector(preprocessed_abstract))

0 0.0003323554992675781 1 53.33499789237976 2 103.42720293998718 3 153.6304588317871 4 202.39628386497498 5 251.3199815750122 6 298.7749104499817 7 346.5766522884369 8 399.88684272766113 9 461.1836185455322 10 513.5033805370331 11 564.1100103855133 12 616.11439204216 

In [59]:
len(author_list)

1560120

In [95]:
pickle.dump(dict(author_vector_dict),open("pickles/author_vector_dict_dl.pkl","wb"))

BrokenPipeError: [Errno 32] Broken pipe

In [90]:
print(author_vector_dict[author_list[0]])


{'Nathalie Gaussier': 'Starting from neurobiological hypotheses on the existence of place cells (PC) in the brain, the aim of this article is to show how little assumptions at both individual and social levels can lead to the emergence of non-trivial global behaviors in a multi-agent system (MAS). In particular, we show that adding a simple, hebbian learning mechanism on a cognitive map allows autonomous, situated agents to adapt themselves in a dynamically changing environment, and that even using simple agent-following strategies (driven either by similarities in the agent movement, or by individual marks — “signatures” — in agents) can dramatically improve the global performance of the MAS, in terms of survival rate of the agents. Moreover, we show that analogies can be made between such a MAS and the emergence of certain social behaviors.',
 'Ahmadreza Ghaffarizadeh': "Sorting by reversals is a simplified version of the genome rearrangement problem that seeks to discover the evolut

In [2]:
main_df =  pd.read_json("jsons/final_df.json")

In [4]:
main_df.head()

Author1                                                 X1  \
0            F.C. Williams  [0.364787668, 0.6471684575000001, -1.028962373...   
1                 Hao Wang  [1.4861617088, -1.926681757, -5.0331339836, -3...   
10           Ernest Hirsch  [0.8073499799, -0.4719045758, -3.3288636208, -...   
100              Ray Tsaih  [0.4020751715, -0.398655951, -3.9636628628, -1...   
1000  Edward W. Chencinski  [1.7232670784000002, -0.7030912042, -3.8556978...   

                Author2                                                 X2  \
0            T. Kilburn  [0.6759288311, 0.0381897353, -0.9558166862, -0...   
1     J. Barkley Rosser  [-0.08969531210000001, -0.4748720825, -3.68153...   
10     Redouane Khemmar  [0.3839387596, -0.9602490664000001, -2.3537962...   
100        Wan‐Ying Lin  [0.2723645568, -1.6571266651, -3.6135985851, -...   
1000    Markus M. Helms  [1.6385244131, -1.423461318, -3.2316505909, -3...   

             y  
0     0.000000  
1     0.000005  
10    0.000820  
100   0.003284  
1000  0.003532

In [7]:
main_df['Author1']=main_df['Author1'].apply(lambda row:np.array(row))
main_df['Author2']=main_df['Author2'].apply(lambda row:np.array(row))

In [ ]:
main_df.to_json("jsons/final_df1.json")

In [13]:
main_df.reset_index(drop=True,inplace=True)

In [15]:
main_df['x1']=main_df.apply(lambda row:author_vector_dict[row.Author1], axis=1)
main_df['x2']=main_df.apply(lambda row:author_vector_dict[row.Author2], axis=1)

In [23]:
main_df.rename(index=str, columns={"Score":"y","x1": "X1", "x2": "X2"},inplace=True)

In [30]:
cols=['Author1','X1','Author2','X2','y']
main_df=main_df[cols]

In [33]:
main_df

Author1  \
0                        F.C. Williams   
1                             Hao Wang   
2                         Max H. Kraus   
3                          John Jacobs   
4                       Clark Weissman   
5        Jean-pierre Henri Van Uffelen   
6                        Jay Glicksman   
7                       Ching-Long Yeh   
8                            Fabio Kon   
9                       Alex Lallement   
10                       Ernest Hirsch   
11                      Alex Lallement   
12             Antonio Ramírez-Treviño   
13                  Elvia Ruiz-Beltrán   
14                        Bingyi Zhang   
15                        Jeffrey Heer   
16                Konstantinos Bletsas   
17                     Bruce L. Hitson   
18                        Caixia Zhang   
19                          Daqing Xue   
20                        Caixia Zhang   
21                        Caixia Zhang   
22                          Daqing Xue   
23                Michael N. Katehakis   
24                    Benjamin Melamed   
25                    Benjamin Melamed   
26                          Hagbae Kim   
27                          Ho Jae Lee   
28                     Bruce L. Hitson   
29                          Hagbae Kim   
...                                ...   
7499012               Kazuya Tsukamoto   
7499013               Kazuya Tsukamoto   
7499014                   Amit Thawani   
7499015                     K. Mueller   
7499016                Bernhard Kaspar   
7499017                     K. Mueller   
7499018                     K. Mueller   
7499019                      A. Smolic   
7499020                Bruce L. Hitson   
7499021                      A. Smolic   
7499022                      A. Smolic   
7499023                      A. Smolic   
7499024                Bernhard Kaspar   
7499025                   Peter Eisert   
7499026                 Philipp Merkle   
7499027                Bernhard Kaspar   
7499028                Bernhard Kaspar   
7499029                   Peter Eisert   
7499030                Michele Boreale   
7499031                  Jay Glicksman   
7499032                  A. H. Davison   
7499033                    Jye-Chyi Lu   
7499034                Christian Bunse   
7499035                Christian Bunse   
7499036                      Jörg Dörr   
7499037                 Michael Kahane   
7499038                Itamar Elhanany   
7499039                  Kenji Shimada   
7499040                 Steven J. Owen   
7499041                  Kenji Shimada   

                                                        X1  \
0        [0.36478767, 0.64716846, -1.0289624, -0.140485...   
1        [1.4861617, -1.9266818, -5.033134, -3.6864588,...   
2        [0.5783666, -0.0004665713, -0.22290942, -0.243...   
3        [0.04955625, -0.07910657, -0.9593276, -0.58803...   
4        [0.9536578, -0.65992296, -2.7825944, -1.485245...   
5        [-0.25998595, 0.47584343, -1.5436379, -0.64330...   
6        [1.1150359, -1.9513988, -1.7446333, -1.2634867...   
7        [2.887437, -1.7677239, -3.9025588, -1.4722933,...   
8        [3.1321616, -3.006311, -4.4729314, -2.784296, ...   
9        [0.59897697, -0.74744695, -2.1262484, -0.09517...   
10       [0.80735, -0.47190458, -3.3288636, -1.9487354,...   
11       [0.59897697, -0.74744695, -2.1262484, -0.09517...   
12       [1.8817339, -0.08498864, -5.4989986, -4.116237...   
13       [-0.46162283, -0.39681906, -2.6229494, -0.8137...   
14       [0.4808013, 0.66038513, -2.662808, -1.1307361,...   
15       [3.2762287, -2.4736967, -4.140653, -0.7632603,...   
16       [2.8456674, 0.9731625, -2.4305422, -2.2698553,...   
17       [0.33536366, -0.9748886, -1.4350103, -0.704203...   
18       [1.3110785, -0.6023875, -4.1391, -1.9450401, -...   
19       [1.6314247, 0.3454629, -2.8644338, -1.2376924,...   
20       [1.3110785, -0.6023875, -4.1391, -1.9450401, -...   
21       [1.3110785, -0.6023875, -4.1391, -1.9450401, -...   


In [32]:
main_df.to_json("jsons/final_df.json")